### Interactive Choropleth Map
This notebook generates a set of interactive choropleth maps, showing various metrics of internet quality for different areas in the Province of Alberta. These maps attempt to reconcile all boundaries given in the competition data. Some boundaries were cut into, or overlapped, but parts of the dataset eventually had to be discarded.

In [1]:
import geopandas as gpd
import pandas as pd
from pathlib import Path
import shapely

from folium import Choropleth, Marker
import folium

from helper_functions import show_overlaps, boundary_cut, plot_bounds

### Boundary Data

In [2]:
file_path = Path("data/Municipal_Boundaries_SHP_Geographic/")

In [3]:
rural_gdf = gpd.read_file(file_path/"RURAL.shp") #1 
reserve_gdf = gpd.read_file(file_path/"INDIAN.shp") # 2
city_gdf = gpd.read_file(file_path/"CITY.shp") # 3
town_gdf = gpd.read_file(file_path/"TOWN.shp") # 4 
urbserv_gdf = gpd.read_file(file_path/"urbserv.shp") # 5
# hamlet_df = gpd.read_file(file_path/"HAMLETPT.shp") # points, no boundaries
village_gdf = gpd.read_file(file_path/"VILLAGE.shp") # 6
svillage_gdf = gpd.read_file(file_path/"SVILLAGE.shp") # 7 

### Internet Data

In [4]:
ookla_gdf = gpd.read_file("data/ookla/AB_ookla_data_2020.shp")

In [5]:
ookla_gdf.head(3)

quadkey  avg_d_kbps  avg_u_kbps  avg_lat_ms  tests  devices  \
0  0212113033010133         807         273          84      1        1   
1  0212113123020220       82062       11294          19     34        4   
2  0212131212333013        9741        1382          24      7        2   

  quarter conn_type                                           geometry  
0      Q1     fixed  POLYGON ((-114.13147 53.53051, -114.12598 53.5...  
1      Q1     fixed  POLYGON ((-113.55469 53.46843, -113.54919 53.4...  
2      Q1     fixed  POLYGON ((-114.28528 51.20344, -114.27979 51.2...

### Processing Data

Changing ookla polygons to centroids, for spatial join accuracy.

In [6]:
ookla_gdf["long"] = ookla_gdf.geometry.apply(lambda x:x.centroid.x)
ookla_gdf["lat"] = ookla_gdf.geometry.apply(lambda x:x.centroid.y)

In [7]:
ookla_temp = pd.DataFrame(ookla_gdf.drop("geometry", axis=1))
ookla_gdf = gpd.GeoDataFrame(ookla_temp, geometry=gpd.points_from_xy(
    ookla_temp.long, ookla_temp.lat))
ookla_gdf = ookla_gdf.drop(["long", "lat"], axis=1)

In [8]:
ookla_gdf.crs = {"init":"EPSG:4326"}

/home/peter/anaconda3/envs/basic-data/lib/python3.8/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))


Cutting smaller boundaries out of the rural boundaries

In [9]:
rural_cuts = [reserve_gdf, city_gdf, town_gdf, urbserv_gdf, village_gdf, svillage_gdf] 

In [10]:
rural_gdf = boundary_cut(rural_cuts, rural_gdf)

Cutting smaller boundaries out of reserve boundaries

In [11]:
reserve_cuts = rural_cuts.copy()
reserve_cuts.remove(reserve_gdf)

In [12]:
reserve_gdf = boundary_cut(reserve_cuts, reserve_gdf)

Spatial joining data points with boundaries

In [18]:
rural_data = gpd.sjoin(ookla_gdf, rural_gdf.to_crs("+init=epsg:4326 +type=crs"))

/home/peter/anaconda3/envs/basic-data/lib/python3.8/site-packages/pyproj/crs/crs.py:280: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  projstring = _prepare_from_string(projparams)


In [19]:
reserve_data = gpd.sjoin(ookla_gdf, reserve_gdf.to_crs("+init=epsg:4326 +type=crs"))

/home/peter/anaconda3/envs/basic-data/lib/python3.8/site-packages/pyproj/crs/crs.py:280: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  projstring = _prepare_from_string(projparams)


In [20]:
reserve_gdf["area"] = reserve_gdf.to_crs({'init':'epsg:3857'})["geometry"].area / (10 ** 6)

/home/peter/anaconda3/envs/basic-data/lib/python3.8/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))


In [21]:
test_counts = pd.DataFrame(columns=["GEONAME"])

In [22]:
test_counts = reserve_data.GEONAME.value_counts().to_frame().reset_index()
test_counts = test_counts.rename(columns={"index":"GEONAME", "GEONAME":"test_count"})

In [23]:
reserve_gdf.shape

(297, 6)

In [24]:
reserve_gdf = reserve_gdf.merge(test_counts, how="outer")

In [25]:
reserve_gdf = reserve_gdf.fillna(0)

In [26]:
# largest reserves
problem_rows1 = [289, 249, 217, 71, 81, 275, 283, 163, 27, 159]
working_rows1 =  list(reserve_gdf["area"].sort_values(ascending=False).index[:90]) # works to 80
for row in problem_rows1:
    try:
        working_rows1.remove(row)
    except:
        pass
reserve_gdf.sort_values("area", ascending=False)[85:90] # indian id is index + 1

INDIAN_ID    PID                              GEONAME GEOCODE  \
61          62  34335           BLOOD INDIAN RESERVE #148A    0557   
283        284  34569      FORT MCKAY INDIAN RESERVE #174C    4046   
163        164  34275         O'CHIESE INDIAN RESERVE #203    0903   
27          28  34176        TALLCREE INDIAN RESERVE #173A    0495   
20          21  34145  UPPER HAY RIVER INDIAN RESERVE #212    0493   

                                              geometry       area  test_count  
61   POLYGON ((-113.69055 49.04908, -113.69059 49.0...  45.267938         0.0  
283  POLYGON ((-111.44163 57.38100, -111.44162 57.3...  44.757691         0.0  
163  POLYGON ((-115.28302 52.68929, -115.28303 52.6...  43.068350        35.0  
27   POLYGON ((-115.64487 58.06456, -115.65850 58.0...  40.999415         0.0  
20   POLYGON ((-117.75487 59.04563, -117.75516 59.0...  40.090234         0.0

Changing dataframe formats to be used in the folium map:

In [27]:
# is it possible to get the reserve populations, and maybe sort by speed per density?

In [28]:
# reserves with most tests
problem_rows2 = [175, 177, 206, 209, 208, 205, 204, 291, 292, 293]
working_rows2 = list(reserve_gdf["test_count"].sort_values(ascending=False).index[:17])
for row in problem_rows2:
    try:
        working_rows2.remove(row)
    except:
        pass

In [29]:
reserve_data = gpd.sjoin(ookla_gdf, reserve_gdf.to_crs("+init=epsg:4326 +type=crs"))

/home/peter/anaconda3/envs/basic-data/lib/python3.8/site-packages/pyproj/crs/crs.py:280: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  projstring = _prepare_from_string(projparams)


In [30]:
reserve_gdf.sort_values("test_count", ascending=False)[10:17] # indian id is index + 1

INDIAN_ID    PID                                  GEONAME GEOCODE  \
208        209  34599              SIKSIKA INDIAN RESERVE #146    0918   
205        206  34600              SIKSIKA INDIAN RESERVE #146    0918   
204        205  34400              SIKSIKA INDIAN RESERVE #146    0918   
290        291  34368  STONEY INDIAN RESERVES #142, #143, #144    4893   
291        292  34371  STONEY INDIAN RESERVES #142, #143, #144    4893   
292        293  34370  STONEY INDIAN RESERVES #142, #143, #144    4893   
293        294  34369  STONEY INDIAN RESERVES #142, #143, #144    4893   

                                              geometry         area  \
208  POLYGON ((-113.29931 50.83610, -113.29749 50.8...     0.215541   
205  POLYGON ((-113.26052 50.80519, -113.25968 50.8...     6.469828   
204  POLYGON ((-113.13237 50.89081, -113.12564 50.8...  1784.900453   
290  POLYGON ((-114.79153 51.20453, -114.79142 51.2...     3.296523   
291  POLYGON ((-114.74966 51.20332, -114.75407 51.2...     4.497231   
292  POLYGON ((-114.74570 51.21863, -114.76301 51.2...     6.131160   
293  POLYGON ((-114.77528 51.22103, -114.77370 51.2...     2.667002   

     test_count  
208       121.0  
205       121.0  
204       121.0  
290        60.0  
291        60.0  
292        60.0  
293        60.0

In [ ]:
# drop all working rows?
broken_reserve_final = 

In [33]:
rural_dict = rural_data.groupby("GEONAME")["avg_d_kbps"].mean()
reserve_dict = reserve_data.groupby("GEONAME")["avg_d_kbps"].mean()

In [49]:
rural_final = rural_gdf[["GEONAME", "geometry"]].set_index("GEONAME")
reserve_final1 = reserve_gdf.iloc[working_rows1][["GEONAME", "geometry"]].set_index("GEONAME")

In [50]:
reserve_final2 = reserve_gdf.iloc[working_rows2][["GEONAME", "geometry"]].set_index("GEONAME")

In [60]:
reserve_final1.unique

AttributeError: 'GeoDataFrame' object has no attribute 'unique'

### Average Download Speed Plot

In [55]:
m_test = folium.Map(location=[55,-115], tiles='cartodbpositron', zoom_start=5, width="60%", height="100%")

# Choropleth(geo_data=rural_final.__geo_interface__, 
#            data=rural_dict, 
#            key_on="feature.id", 
#            fill_color='YlGnBu', 
#            line_weight=0.5,
#            legend_name='Internet Test Numbers'
#           ).add_to(m_test)

Choropleth(geo_data=reserve_final.__geo_interface__, 
           data=reserve_dict, 
           key_on="feature.id", 
           fill_color='YlGnBu', 
           line_weight=0.5,
           legend_name='Internet Test Numbers'
          ).add_to(m_test)

m_test